### 크롤링을 통한 중고차 데이터 셋 확보
https://github.com/sobin98/used_car_prediction/blob/main/webcrawling_usedcar.py#L1
- https://velog.io/@sobing/usedCarPrediction

In [2]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import time
from selenium import webdriver
from selenium.webdriver import Keys
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager


# 크롬 웹드라이버 설치 및 설정
Chrome_options = webdriver.ChromeOptions()

In [3]:
# 웹페이지에서 우리 컴이 봇으로 인식하지 못하게 하기 위한 작업 
# 인터넷에 user agent string 치고 각자 컴퓨터에 맞게 설정

user_agent = 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.0.0 Safari/537.36'
Chrome_options.add_argument('user-agent=' + user_agent)

In [4]:
Chrome_options.add_experimental_option('detach', True)
driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()),options=Chrome_options)
driver.maximize_window()

### 모델명별 차량 추출

In [13]:
# 현대 : 그랜저, 스타랙스, 포터, 아반떼, 쏘나타, 싼타페.| 제네시스 : G80, G90, | 기아 : 카니발, 봉고, k7, 레이, 모닝 |
# 쉐보레/대우 | 삼성 (르노) | 수입: 벤츠 : E클래스, s클, 마이바흐 s클, g바겐, 포르쉐 : 911, 카이엔, 파나메라, |

totalurl = [("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=5&page=1&order=S11&view_size=20", 7),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=17&page=1&order=S11&view_size=20", 5),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=42&page=1&order=S11&view_size=20", 5),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=22&page=1&order=S11&view_size=20", 4),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=21&page=1&order=S11&view_size=20", 3),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=20&page=1&order=S11&view_size=20", 2),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=1010&group_no=893&page=1&order=S11&view_size=20", 4),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=1010&group_no=893&page=1&order=S11&view_size=20", 4),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=3&group_no=76&page=1&order=S11&view_size=20", 9),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=3&group_no=59&page=1&order=S11&view_size=20", 4),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=3&group_no=45&page=1&order=S11&view_size=20", 3),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=3&group_no=50&page=1&order=S11&view_size=20", 2),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=3&group_no=55&page=1&order=S11&view_size=20", 2),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=8&page=1&order=S11&view_size=20", 7),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=26&page=1&order=S11&view_size=20", 5),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=I&maker_no=21&group_no=356&page=1&order=S11&view_size=20", 6),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=I&maker_no=21&group_no=358&page=1&order=S11&view_size=20", 16),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=I&maker_no=21&group_no=359&page=1&order=S11&view_size=20", 5),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=I&maker_no=21&group_no=362&page=1&order=S11&view_size=20", 8),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=I&maker_no=43&group_no=250&page=1&order=S11&view_size=20", 10),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=I&maker_no=43&group_no=251&page=1&order=S11&view_size=20", 7),
       ("https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=I&maker_no=43&group_no=252&page=1&order=S11&view_size=20", 6)
      ]
df_cars=[]
# totalurl = f'https://www.bobaedream.co.kr/cyber/CyberCar.php?gubun=K&page={keyword}&order=S11&view_size=70'
urls=[]
for i in totalurl:
    pagenum=i[1]
    for j in range(pagenum):
        url=i[0].format(str(j))
        urls.append(url)
# headers = {'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.0.0 Safari/537.36'}
urls

['https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=5&page=1&order=S11&view_size=20',
 'https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=5&page=1&order=S11&view_size=20',
 'https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=5&page=1&order=S11&view_size=20',
 'https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=5&page=1&order=S11&view_size=20',
 'https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=5&page=1&order=S11&view_size=20',
 'https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=5&page=1&order=S11&view_size=20',
 'https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=5&page=1&order=S11&view_size=20',
 'https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_no=17&page=1&order=S11&view_size=20',
 'https://www.bobaedream.co.kr/mycar/mycar_list.php?gubun=K&maker_no=49&group_n

### 보배드림 사이트(중고차 사이트) 크롤링 

In [22]:
info=["이름","차량번호","링크","연식","주행거리","연료","배기량","색상","보증정보","가격","신차대비가격"]

coloptions=["옵션_선루프","옵션_파노라마선루프","옵션_열선앞","옵션_열선뒤","옵션_전방센서"
     ,"옵션_후방센서","옵션_전방캠","옵션_후방캠","옵션_어라운드뷰","옵션_네비순정"]

findoptions=["선루프","파노라마선루프","열선시트(앞좌석)","열선시트(뒷좌석)","전방센서"
     ,"후방센서","전방카메라","후방카메라","어라운드뷰","네비게이션(순정)"]
colacci_info1=["보험이력등록","소유자변경횟수","사고상세_전손","사고상세_침수전손","사고상세_침수분손","사고상세_도난","보험_내차피해(횟수)","보험_내차피해(가격)","사고상세_타차가해(횟수)","보험_타차피해(가격)"]

cols=info+coloptions+colacci_info1 #분석과정에서 아웃라이어의 판별여부를 위해 링크추가

headers = {'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.0.0 Safari/537.36'}

#옵션이름 받아서 확인여부하는 함수
def option_check(soupobject,option_name):
    check = soupobject.find("button", text=option_name).find_parent().find_previous_sibling().get_attribute_list('checked')
    
    if check[0]=='':
        time.sleep(1)
        return '유'
    else:
        time.sleep(1)
        return '무'
        
for url in urls:
    # res = driver.get(url)
    # driver.implicitly_wait(5)
    # time.sleep(1)
    try:
        res=requests.get(url, headers = headers)
        res.raise_for_status()
        soup=BeautifulSoup(res.text,"lxml")
        cars=soup.find_all("li",attrs={"class":"product-item"})
    
    # requests.adapters.DEFAULT_RETRIES = 10
    except:
        time.sleep(2)
        res=requests.get(url, headers = headers)
        res.raise_for_status()
        soup=BeautifulSoup(res.text,"lxml")
        cars=soup.find_all("li",attrs={"class":"product-item"})

    
    
    links=[]
    #한 url마다 들어있는 모든 차들에 대해 실행
    for car in cars:
        link = "https://www.bobaedream.co.kr" + car.a["href"]
        
        links.append(link)
    for link in links:
        print(link)
        try:

        
            res2=requests.get(link, headers = headers)
            res2.raise_for_status()
            
            soup2 = BeautifulSoup(res2.text, "lxml")
            infobox = soup2.find("div", attrs={"class": "info-util box"})

        except:
            time.sleep(1)
            res2=requests.get(link, headers = headers)
            res2.raise_for_status()
            
            soup2 = BeautifulSoup(res2.text, "lxml")
            infobox = soup2.find("div", attrs={"class": "info-util box"})

        try:
            ratiopr = infobox.find("b")
        except:
            continue
        
        name=soup2.find("h3",attrs={"class":"tit"})
        state=soup2.find("div",attrs={"class":"tbl-01 st-low"})
        galdata=soup2.find("div",attrs={"class":"gallery-data"})
        carnumber=galdata.find("b")
        
        year=state.find("th",text='연식').find_next_sibling("td")
        km=state.find("th",text='주행거리').find_next_sibling("td")
        fuel=state.find("th",text='연료').find_next_sibling("td")
        amount=state.find("th",text='배기량').find_next_sibling("td")
        color=state.find("th",text='색상').find_next_sibling("td")
        guarn=state.find("b",text='보증정보').find_next("td")
        price=soup2.find("span",attrs={"class":"price"})
        time.sleep(1)
        option_table=soup2.find("div",attrs={"class":"tbl-option"})
        checkoptions=[]
        if option_table.find("th",text='외관')!=None:
            for option in findoptions:
                checkoptions.append(option_check(option_table,option))
                
        else:
            checkoptions=['']*len(coloptions)

        if infobox.find("span",attrs={"class":"round-ln insurance"}).find_next("i").find_next("em")==None:
            acc1 = '미등록'
        else:
            acc1 = '등록'

        findacci_info1=[]
        try:
            if acc1=='등록':
                acc1table=soup2.find("div",attrs={"class":"info-insurance"})
                try:
                    insurdt1 = acc1table.find("th", text="Vehicle number/owner change").find_next_sibling("td").get_text()[-2]
                except AttributeError:
                    insurdt1 = ''

                try:
                    insuraccis1 = acc1table.find("th", text="auto insurance special accident").find_next_sibling("td").get_text().split('/')
                    insurdt2 = insuraccis1[0][-2]
                    insurdt3 = insuraccis1[1][-2]
                    insurdt4 = insuraccis1[2][-2]
                    insurdt5 = insuraccis1[3][-1]
                except (AttributeError, IndexError):
                    insurdt2 = ''
                    insurdt3 = ''
                    insurdt4 = ''
                    insurdt5 = ''

                try:
                    insuraccis2 = acc1table.find("th", text="Insurance accident (insurance damage)").find_next_sibling("td").get_text().split('time')
                    insurdt6 = insuraccis2[0]
                    insurdt7 = insuraccis2[1][2:-2]
                except (AttributeError, IndexError):
                    insurdt6 = ''
                    insurdt7 = ''

                try:
                    insuraccis3 = acc1table.find("th", text="Insurance accident (other damage)").find_next_sibling("td").get_text().split('time')
                    insurdt8 = insuraccis3[0]
                    insurdt9 = insuraccis3[1][2:-2]
                except (AttributeError, IndexError):
                    insurdt8 = ''
                    insurdt9 = ''

                findacci_info1 = [insurdt1, insurdt2, insurdt3, insurdt4, insurdt5, insurdt6, insurdt7, insurdt8, insurdt9]

            else:
                findacci_info1=['']*(len(colacci_info1)-1)
        except IndexError:
                findacci_info1 = ['']*(len(colacci_info1)-1)

        temp=[name.get_text(),carnumber.get_text(),link,year.get_text(),km.get_text(),fuel.get_text(),amount.get_text(),
          color.get_text(),guarn.get_text(),price.get_text(),ratiopr.get_text()]+checkoptions+[acc1]+findacci_info1
        df_cars.append(temp)
        
df_cars=pd.DataFrame(data=df_cars,columns=cols)
df_cars.to_csv('cars.csv')
print(df_cars.head())

https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2204651&gubun=K


C:\Users\user\AppData\Local\Temp\ipykernel_16132\320166177.py:80: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  year=state.find("th",text='연식').find_next_sibling("td")
C:\Users\user\AppData\Local\Temp\ipykernel_16132\320166177.py:81: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  km=state.find("th",text='주행거리').find_next_sibling("td")
C:\Users\user\AppData\Local\Temp\ipykernel_16132\320166177.py:82: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  fuel=state.find("th",text='연료').find_next_sibling("td")
C:\Users\user\AppData\Local\Temp\ipykernel_16132\320166177.py:83: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  amount=state.find("th",text='배기량').find_next_sibling("td")
C:\Users\user\AppData\Local\Temp\ipykernel_16132\320166177.py:84: DeprecationWarning: The 'text' argu

https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2204199&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2202297&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2204768&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2204163&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2199001&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2205040&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2202044&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2202610&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2202609&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2194808&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2199404&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2203988&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2203990&gubun=K
https://www.bobaedream.co.kr/mycar/mycar_view.php?no=2205279&gubun=K
https://www.bobaedream.co.kr/mycar

In [23]:
df = pd.read_csv('cars.csv')
df

Unnamed: 0                                  이름           차량번호  \
0              0  현대 그랜저IG 하이브리드 2.4 HEV  익스클루시브 스페셜   차량번호 37누3541   
1              1      현대 더 뉴 그랜저 하이브리드 2.4 HEV 캘리그래피  차량번호 156마6718   
2              2           현대 더 뉴 그랜저 3.0 LPi   프리미엄  차량번호 153오1506   
3              3              현대 더 럭셔리 그랜저 Q270 LPi    차량번호 05마5118   
4              4            현대 더 뉴 그랜저 2.5  프리미엄 초이스  차량번호 162허3154   
...          ...                                 ...            ...   
2479        2479            포르쉐 파나메라 2세대  3.0 4 -     차량번호 103서9045   
2480        2480     포르쉐 파나메라 2세대  2.9 4 이그제큐티브 -     차량번호 255머1522   
2481        2481                   포르쉐 파나메라 2세대 3.0    차량번호 62어9416   
2482        2482            포르쉐 파나메라 2세대  3.0 4 -     차량번호 180어8080   
2483        2483          포르쉐 파나메라 1세대  4.8 GTS -      차량번호 15거6116   

                                                     링크              연식  \
0     https://www.bobaedream.co.kr/mycar/mycar_view....  2017.05 (18년형)   
1     https://www.bobaedream.co.kr/mycar/mycar_view....  2020.11 (21년형)   
2     https://www.bobaedream.co.kr/mycar/mycar_view....  2021.09 (22년형)   
3     https://www.bobaedream.co.kr/mycar/mycar_view....  2009.09 (10년형)   
4     https://www.bobaedream.co.kr/mycar/mycar_view....         2020.06   
...                                                 ...             ...   
2479  https://www.bobaedream.co.kr/mycar/mycar_view....         2018.02   
2480  https://www.bobaedream.co.kr/mycar/mycar_view....         2021.05   
2481  https://www.bobaedream.co.kr/mycar/mycar_view....         2018.03   
2482  https://www.bobaedream.co.kr/mycar/mycar_view....         2019.09   
2483  https://www.bobaedream.co.kr/mycar/mycar_view....         2014.11   

            주행거리         연료               배기량    색상              보증정보  ...  \
0      70,530 km  가솔린 하이브리드  2,359 cc (199마력)   검정색                만료  ...   
1      46,128 km  가솔린 하이브리드  2,359 cc (200마력)   진회색  60개월 / 100,000km  ...   
2      21,062 km        LPG  2,999 cc (235마력)    흰색              정보없음  ...   
3     162,000 km        LPG  2,656 cc (165마력)   검정색                만료  ...   
4      21,190 km        가솔린  2,497 cc (198마력)   검정색              정보없음  ...   
...          ...        ...               ...   ...               ...  ...   
2479   30,500 km        가솔린  2,995 cc (330마력)    회색                만료  ...   
2480    5,000 km        가솔린  2,894 cc (336마력)   검정색  48개월 / 999,999km  ...   
2481   15,153 km        가솔린  2,995 cc (330마력)   파란색                만료  ...   
2482    8,000 km        가솔린  2,995 cc (330마력)    흰색  48개월 / 999,999km  ...   
2483  111,000 km        가솔린  4,806 cc (440마력)  기타색상                불가  ...   

     보험이력등록 소유자변경횟수 사고상세_전손 사고상세_침수전손 사고상세_침수분손 사고상세_도난 보험_내차피해(횟수)  \
0        등록     NaN     NaN       NaN       NaN     NaN         NaN   
1        등록     NaN     NaN       NaN       NaN     NaN         NaN   
2        등록     NaN     NaN       NaN       NaN     NaN         NaN   
3        등록     NaN     NaN       NaN       NaN     NaN         NaN   
4        등록     NaN     NaN       NaN       NaN     NaN         NaN   
...     ...     ...     ...       ...       ...     ...         ...   
2479     등록     NaN     NaN       NaN       NaN     NaN         NaN   
2480    미등록     NaN     NaN       NaN       NaN     NaN         NaN   
2481     등록     NaN     NaN       NaN       NaN     NaN         NaN   
2482    미등록     NaN     NaN       NaN       NaN     NaN         NaN   
2483    미등록     NaN     NaN       NaN       NaN     NaN         NaN   

     보험_내차피해(가격) 사고상세_타차가해(횟수) 보험_타차피해(가격)  
0            NaN           NaN         NaN  
1            NaN           NaN         NaN  
2            NaN           NaN         NaN  
3            NaN           NaN         NaN  
4            NaN           NaN         NaN  
...          ...           ...         ...  
2479         NaN           NaN         NaN  
2480         NaN           NaN         NaN  
2481         NaN           NaN         NaN  
2482        

### 양질의 데이터 크롤링

In [ ]:
keyword = 200
df_cars=[]
kr_urls = []
foreign_urls = []
for i in range(1, keyword+1):
    kr_urls.append(f'https://www.bobaedream.co.kr/cyber/CyberCar.php?gubun=K&page={i}&order=S11&view_size=70')
    foreign_urls.append(f'https://www.bobaedream.co.kr/cyber/CyberCar.php?gubun=I&page={i}&order=S11&view_size=70')
total_urls = kr_urls + foreign_urls


info=["이름","차량번호","링크","연식","주행거리","연료","배기량","색상","보증정보","가격","신차대비가격"]

coloptions=["옵션_선루프","옵션_파노라마선루프","옵션_열선앞","옵션_열선뒤","옵션_전방센서"
     ,"옵션_후방센서","옵션_전방캠","옵션_후방캠","옵션_어라운드뷰","옵션_네비순정"]

findoptions=["선루프","파노라마선루프","열선시트(앞좌석)","열선시트(뒷좌석)","전방센서"
     ,"후방센서","전방카메라","후방카메라","어라운드뷰","네비게이션(순정)"]
colacci_info1=["보험이력등록","소유자변경횟수","사고상세_전손","사고상세_침수전손","사고상세_침수분손","사고상세_도난","보험_내차피해(횟수)","보험_내차피해(가격)","사고상세_타차가해(횟수)","보험_타차피해(가격)"]

cols=info+coloptions+colacci_info1 #분석과정에서 아웃라이어의 판별여부를 위해 링크추가

headers = {'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.0.0 Safari/537.36'}

#옵션이름 받아서 확인여부하는 함수
def option_check(soupobject,option_name):
    check = soupobject.find("button", text=option_name).find_parent().find_previous_sibling().get_attribute_list('checked')
    
    if check[0]=='':
        time.sleep(1)
        return '유'
        
    else:
        time.sleep(1)
        return '무'
        
        
for url in total_urls:

    try:
        res=requests.get(url, headers = headers)
        res.raise_for_status()
        soup=BeautifulSoup(res.text,"lxml")
        cars=soup.find_all("li",attrs={"class":"product-item"})
    
    # requests.adapters.DEFAULT_RETRIES = 10
    except:
        time.sleep(2)
        res=requests.get(url, headers = headers)
        res.raise_for_status()
        soup=BeautifulSoup(res.text,"lxml")
        cars=soup.find_all("li",attrs={"class":"product-item"})

    
    
    links=[]
    #한 url마다 들어있는 모든 차들에 대해 실행
    for car in cars:
        link = "https://www.bobaedream.co.kr" + car.a["href"]
        
        links.append(link)
    for link in links:
        print(link)
        try:

        
            res2=requests.get(link, headers = headers)
            res2.raise_for_status()
            
            soup2 = BeautifulSoup(res2.text, "lxml")
            infobox = soup2.find("div", attrs={"class": "info-util box"})

        except:
            time.sleep(1)
            res2=requests.get(link, headers = headers)
            res2.raise_for_status()
            
            soup2 = BeautifulSoup(res2.text, "lxml")
            infobox = soup2.find("div", attrs={"class": "info-util box"})

        try:
            ratiopr = infobox.find("b")
        except:
            continue
        
        name=soup2.find("h3",attrs={"class":"tit"})
        state=soup2.find("div",attrs={"class":"tbl-01 st-low"})
        galdata=soup2.find("div",attrs={"class":"gallery-data"})
        carnumber=galdata.find("b")
        time.sleep(0.5)
        year=state.find("th",text='연식').find_next_sibling("td")
        km=state.find("th",text='주행거리').find_next_sibling("td")
        fuel=state.find("th",text='연료').find_next_sibling("td")
        amount=state.find("th",text='배기량').find_next_sibling("td")
        color=state.find("th",text='색상').find_next_sibling("td")
        guarn=state.find("b",text='보증정보').find_next("td")
        price=soup2.find("span",attrs={"class":"price"})
        
        option_table=soup2.find("div",attrs={"class":"tbl-option"})
        checkoptions=[]
        if option_table.find("th",text='외관')!=None:
            for option in findoptions:
                checkoptions.append(option_check(option_table,option))
                
        else:
            checkoptions=['']*len(coloptions)

        if infobox.find("span",attrs={"class":"round-ln insurance"}).find_next("i").find_next("em")==None:
            acc1 = '미등록'
        else:
            acc1 = '등록'

        findacci_info1=[]
        try:
            if acc1=='등록':
                acc1table=soup2.find("div",attrs={"class":"info-insurance"})
                try:
                    insurdt1 = acc1table.find("th", text="Vehicle number/owner change").find_next_sibling("td").get_text()[-2]
                except AttributeError:
                    insurdt1 = ''

                try:
                    insuraccis1 = acc1table.find("th", text="auto insurance special accident").find_next_sibling("td").get_text().split('/')
                    insurdt2 = insuraccis1[0][-2]
                    insurdt3 = insuraccis1[1][-2]
                    insurdt4 = insuraccis1[2][-2]
                    insurdt5 = insuraccis1[3][-1]
                except (AttributeError, IndexError):
                    insurdt2 = ''
                    insurdt3 = ''
                    insurdt4 = ''
                    insurdt5 = ''

                try:
                    insuraccis2 = acc1table.find("th", text="Insurance accident (insurance damage)").find_next_sibling("td").get_text().split('time')
                    insurdt6 = insuraccis2[0]
                    insurdt7 = insuraccis2[1][2:-2]
                except (AttributeError, IndexError):
                    insurdt6 = ''
                    insurdt7 = ''

                try:
                    insuraccis3 = acc1table.find("th", text="Insurance accident (other damage)").find_next_sibling("td").get_text().split('time')
                    insurdt8 = insuraccis3[0]
                    insurdt9 = insuraccis3[1][2:-2]
                except (AttributeError, IndexError):
                    insurdt8 = ''
                    insurdt9 = ''

                findacci_info1 = [insurdt1, insurdt2, insurdt3, insurdt4, insurdt5, insurdt6, insurdt7, insurdt8, insurdt9]

            else:
                findacci_info1=['']*(len(colacci_info1)-1)
        except IndexError:
                findacci_info1 = ['']*(len(colacci_info1)-1)

        temp=[name.get_text(),carnumber.get_text(),link,year.get_text(),km.get_text(),fuel.get_text(),amount.get_text(),
          color.get_text(),guarn.get_text(),price.get_text(),ratiopr.get_text()]+checkoptions+[acc1]+findacci_info1
        df_cars.append(temp)
        
df_cars2=pd.DataFrame(data=df_cars,columns=cols)
df_cars2.to_csv('cars2.csv')
print(df_cars2.head())

## 데이터 전처리 EDA

In [6]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns


In [5]:
df = pd.read_csv('cars.csv')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2484 entries, 0 to 2483
Data columns (total 32 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Unnamed: 0     2484 non-null   int64  
 1   이름             2484 non-null   object 
 2   차량번호           2484 non-null   object 
 3   링크             2484 non-null   object 
 4   연식             2484 non-null   object 
 5   주행거리           2484 non-null   object 
 6   연료             2484 non-null   object 
 7   배기량            2484 non-null   object 
 8   색상             2484 non-null   object 
 9   보증정보           2484 non-null   object 
 10  가격             2484 non-null   object 
 11  신차대비가격         2484 non-null   object 
 12  옵션_선루프         2051 non-null   object 
 13  옵션_파노라마선루프     2051 non-null   object 
 14  옵션_열선앞         2051 non-null   object 
 15  옵션_열선뒤         2051 non-null   object 
 16  옵션_전방센서        2051 non-null   object 
 17  옵션_후방센서        2051 non-null   object 
 18  옵션_전방캠  

In [7]:
df.describe()

Unnamed: 0  소유자변경횟수  사고상세_전손  사고상세_침수전손  사고상세_침수분손  사고상세_도난  \
count  2484.000000      0.0      0.0        0.0        0.0      0.0   
mean   1241.500000      NaN      NaN        NaN        NaN      NaN   
std     717.213357      NaN      NaN        NaN        NaN      NaN   
min       0.000000      NaN      NaN        NaN        NaN      NaN   
25%     620.750000      NaN      NaN        NaN        NaN      NaN   
50%    1241.500000      NaN      NaN        NaN        NaN      NaN   
75%    1862.250000      NaN      NaN        NaN        NaN      NaN   
max    2483.000000      NaN      NaN        NaN        NaN      NaN   

       보험_내차피해(횟수)  보험_내차피해(가격)  사고상세_타차가해(횟수)  보험_타차피해(가격)  
count          0.0          0.0            0.0          0.0  
mean           NaN          NaN            NaN          NaN  
std            NaN          NaN            NaN          NaN  
min            NaN          NaN            NaN          NaN  
25%            NaN          NaN            NaN          NaN  
50%            NaN          NaN            NaN          NaN  
75%            NaN          NaN            NaN          NaN  
max            NaN          NaN            NaN          NaN

### 차종명 전처리

In [27]:
def changemodel(str1):
    index1=str1.find(' ')
    index2=str1.find(' ',index1+1)
    index3=str1.find(' ',index2+1)
    return str1[:index3]

def changemodelname(str1):
    if '그랜져' in str1:
        str1=str1.replace("그랜져","그랜저")
        return str1
    else:
        return str1
df['이름']=df['이름'].apply(changemodel).apply(changemodelname)

In [28]:
df.drop(['Unnamed: 0'],axis = 1, inplace = True)
df

이름           차량번호  \
0      현대 그랜저IG 하이브리드   차량번호 37누3541   
1              현대 더 뉴  차량번호 156마6718   
2              현대 더 뉴  차량번호 153오1506   
3            현대 더 럭셔리   차량번호 05마5118   
4              현대 더 뉴  차량번호 162허3154   
5              현대 더 뉴  차량번호 170허8234   
6              현대 더 뉴  차량번호 277부8309   
7        현대 그랜저HG 300   차량번호 01너2361   
8        현대 그랜저IG 3.0   차량번호 36도9568   
9        현대 그랜저HG 300   차량번호 36나0824   
10             현대 더 뉴  차량번호 361서3347   
11           현대 더 럭셔리   차량번호 05마5118   
12     현대 그랜저IG 하이브리드   차량번호 37누3541   
13             현대 더 뉴  차량번호 156마6718   
14             현대 더 뉴  차량번호 153오1506   
15       현대 그랜저HG 240   차량번호 32서1446   
16             현대 더 뉴  차량번호 161조6120   
17             현대 더 뉴  차량번호 115고3961   
18             현대 더 뉴  차량번호 106구4656   
19             현대 더 뉴  차량번호 107너1855   
20             현대 더 뉴  차량번호 152노4306   
21             현대 더 뉴  차량번호 378러9227   
22             현대 더 뉴  차량번호 172버9411   
23     현대 그랜저IG 하이브리드   차량번호 16보3326   
24             현대 더 뉴  차량번호 162허3154   
25             현대 더 뉴  차량번호 170허8234   
26             현대 더 뉴  차량번호 277부8309   
27       현대 그랜저HG 300   차량번호 01너2361   
28       현대 그랜저IG 3.0   차량번호 36도9568   
29       현대 그랜저HG 300   차량번호 36나0824   
30             현대 더 뉴  차량번호 361서3347   
31           현대 더 럭셔리   차량번호 05마5118   
32     현대 그랜저IG 하이브리드   차량번호 37누3541   
33             현대 더 뉴  차량번호 156마6718   
34             현대 더 뉴  차량번호 153오1506   
35       현대 그랜저HG 240   차량번호 32서1446   
36             현대 더 뉴  차량번호 161조6120   
37             현대 더 뉴  차량번호 115고3961   
38             현대 더 뉴  차량번호 106구4656   
39             현대 더 뉴  차량번호 107너1855   
40             현대 더 뉴  차량번호 152노4306   
41             현대 더 뉴  차량번호 378러9227   
42             현대 더 뉴  차량번호 172버9411   
43     현대 그랜저IG 하이브리드   차량번호 16보3326   
44             현대 더 뉴  차량번호 162허3154   
45             현대 더 뉴  차량번호 170허8234   
46             현대 더 뉴  차량번호 277부8309   
47       현대 그랜저HG 300   차량번호 01너2361   
48       현대 그랜저IG 3.0   차량번호 36도9568   
49       현대 그랜저HG 300   차량번호 36나0824   
50             현대 더 뉴  차량번호 361서3347   
51           현대 더 럭셔리   차량번호 05마5118   
52     현대 그랜저IG 하이브리드   차량번호 37누3541   
53             현대 더 뉴  차량번호 156마6718   
54             현대 더 뉴  차량번호 153오1506   
55       현대 그랜저HG 240   차량번호 32서1446   
56             현대 더 뉴  차량번호 161조6120   
57             현대 더 뉴  차량번호 115고3961   
58             현대 더 뉴  차량번호 106구4656   
59             현대 더 뉴  차량번호 107너1855   
60             현대 더 뉴  차량번호 152노4306   
61             현대 더 뉴  차량번호 378러9227   
62             현대 더 뉴  차량번호 172버9411   
63     현대 그랜저IG 하이브리드   차량번호 16보3326   
64             현대 더 뉴  차량번호 162허3154   
65             현대 더 뉴  차량번호 170허8234   
66             현대 더 뉴  차량번호 277부8309   
67       현대 그랜저HG 300   차량번호 01너2361   
68       현대 그랜저IG 3.0   차량번호 36도9568   
69       현대 그랜저HG 300   차량번호 36나0824   
70             현대 더 뉴  차량번호 361서3347   
71           현대 더 럭셔리   차량번호 05마5118   
72     현대 그랜저IG 하이브리드   차량번호 37누3541   
73             현대 더 뉴  차량번호 156마6718   
74             현대 더 뉴  차량번호 153오1506   
75       현대 그랜저HG 240   차량번호 32서1446   
76             현대 더 뉴  차량번호 161조6120   
77             현대 더 뉴  차량번호 115고3961   
78             현대 더 뉴  차량번호 106구4656   
79             현대 더 뉴  차량번호 107너1855   
80             현대 더 뉴  차량번호 152노4306   
81             현대 더 뉴  차량번호 378러9227   
82             현대 더 뉴  차량번호 172버9411   
83     현대 그랜저IG 하이브리드   차량번호 16보3326   
84             현대 디 올  차량번호 163호2060   
85             현대 더 뉴  차량번호 162허3154   
86             현대 더 뉴  차량번호 170허8234   
87             현대 더 뉴  차량번호 277부8309   
88       현대 그랜저HG 300   차량번호 01너2361   
89       현대 그랜저IG 3.0   차량번호 36도9568   
90       현대 그랜저HG 300   차량번호 36나0824   
91             현대 더 뉴  차량번호 361서3347   
92           현대 더 럭셔리   차량번호 05마5118   
93     현대 그랜저IG 하이브리드   차량번호 37누3541   
94             현대 더 뉴  차량번호 156마6718   
95             현대 더 뉴  차량번호 153오1506   
96       현대 그랜저HG 240   차량번호 32서1446   
97             현대 더 뉴  차량번호 161조6120   
98             현대 더 뉴  차량번호 115고3961   
99             현대 더

In [14]:
## 데이터프레임의 모든 행,열 보기
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

### 차량 연식 전처리

In [17]:
def changeyear(string):
    year=int(string[:4])
    month=int(string[5:7])
    n=12*(2022-year)+month
    return n
  
df['연식']=df['연식'].apply(changeyear)

In [26]:
df = pd.read_csv('cars.csv')
df2 = df
df2['연식'].apply()

0       2017.05 (18년형)
1       2020.11 (21년형)
2       2021.09 (22년형)
3       2009.09 (10년형)
4              2020.06
5              2021.04
6              2021.02
7              2014.01
8              2017.01
9       2013.05 (14년형)
10             2020.03
11      2009.09 (10년형)
12      2017.05 (18년형)
13      2020.11 (21년형)
14      2021.09 (22년형)
15      2015.10 (16년형)
16      2021.06 (22년형)
17             2020.03
18             2020.09
19      2020.12 (21년형)
20      2020.10 (21년형)
21             2020.09
22             2020.03
23      2018.12 (19년형)
24             2020.06
25             2021.04
26             2021.02
27             2014.01
28             2017.01
29      2013.05 (14년형)
30             2020.03
31      2009.09 (10년형)
32      2017.05 (18년형)
33      2020.11 (21년형)
34      2021.09 (22년형)
35      2015.10 (16년형)
36      2021.06 (22년형)
37             2020.03
38             2020.09
39      2020.12 (21년형)
40      2020.10 (21년형)
41             2020.09
42             2020.03
43      201

In [30]:
from bs4 import BeautifulSoup
from urllib.request import urlopen
from pandas import Series, DataFrame
import pandas as pd
import sys

def progress(count, total, suffix=''):
    bar_len = 60
    filled_len = int(round(bar_len * count / float(total)))

    percents = round(100.0 * count / float(total), 1)
    bar = '#' * filled_len + '-' * (bar_len - filled_len)

    sys.stdout.write('|%s| %s%s ...%s\r' % (bar, percents, '%', suffix))
    sys.stdout.flush()  # As suggested by Rom Ruben


def get_soup(url):
    html_doc = urlopen(url).read()
    soup = BeautifulSoup(html_doc, 'html.parser')
    return soup


# x = {'a': if }
# x = {key: value for key, value in x.items() if value != 20}
# x



#승용차
def my_car(pagenum):
    site=f"https://www.bobaedream.co.kr/cyber/CyberCar.php?gubun=K&page={str(pagenum)}&order=S11&view_size=70"
    
    soup_wt=get_soup(site)
    info = []
    num_carth=len(soup_wt.find("table",class_="cyber").tbody.find_all("a",class_="sub"))
    for i in range(num_carth):
        soup_wt_detail = get_soup(str('http://www.bobaedream.co.kr')+soup_wt.find("table",class_="cyber").tbody.find_all("a",class_="sub")[i]['href'])
        sp_thing=soup_wt_detail.find("table",class_="specmiddle").tbody.find_all("td")
        s_thing = soup_wt_detail.find("div",class_="information").find_all("span",class_="s")
        td_thing=soup_wt_detail.find("table",class_="spectop").tbody.find_all("td")
        if soup_wt_detail.find("span",class_="fl").find_all("li")==[]:
            d_thing =0
            try:
                temp_dict = {}
                temp_dict = {'a_1.회사':soup_wt_detail.find("div",class_="tit").get_text().replace('\xa0\xa0\xa0','').split(None, 1)[0],
                             'a_2.모델명':soup_wt_detail.find("div",class_="tit").get_text().replace('\xa0\xa0\xa0','').split(None, 1)[1],
                             'b.sell_price(만원)':soup_wt_detail.find("div",class_="information").span.get_text().replace("만원",""),
                             'c.차량번호': s_thing[0].get_text(),
                             'd.연식(년월)': s_thing[1].get_text().replace('\xa0','').replace('년','').replace('월','').split("(")[0],
                             'e.주행거리(km)': s_thing[2].get_text().replace(",","").replace("km","").replace(" ",""),
                             'f.연료': s_thing[3].get_text().replace(",",""),
                             'g_1.배기량(cc)': s_thing[4].get_text().replace(" ","").replace(")","").split("(")[0].replace("cc",""),
                             'g_2.배기량(마력)': s_thing[4].get_text().replace(" ","").replace(")","").split("(")[1].replace("마력",""),
                             'h.변속기': s_thing[5].get_text().replace(",",""),
                             'i.색상': s_thing[6].get_text().replace(",","").replace(" ",""),
                             'j.사고유무': s_thing[7].get_text().replace('(사고이력조회)\n','').replace('\t',''),
                             'k.제조국':td_thing[0].get_text(),
                             'l.출시(년형)' : td_thing[1].get_text().split("/")[0].replace("년",""),
                             'm.신차가격(만원)' : td_thing[2].get_text().replace(',','').replace("만원",""),
                             'n.번호변경횟수' : "0",
                             'o.소유자변경횟수' : "0",
                             'p.보험사고이력(내차피해)_c' :  "0",
                             'q.보험사고이력(내차피해)_m' :  "0",
                             'r.보험사고이력(타차가해)_c' :  "0",
                             's.보험사고이력(타차가해)_m' :  "0",
                             't.연비(km/l)' : sp_thing[3].get_text().replace("km/ℓ",""),
                             'u.구동방식' : sp_thing[10].get_text().replace(" ",""),
                             'v.보디형식' : sp_thing[11].get_text(),
                             'w.변속기' : sp_thing[12].get_text()}     
                info.append(temp_dict)

            except:
                pass           
            
        else:
            
            d_thing = soup_wt_detail.find("span",class_="fl").find_all("li")

            try:
                temp_dict = {}
                temp_dict = {'a_1.회사':soup_wt_detail.find("div",class_="tit").get_text().replace('\xa0\xa0\xa0','').split(None, 1)[0],
                             'a_2.모델명':soup_wt_detail.find("div",class_="tit").get_text().replace('\xa0\xa0\xa0','').split(None, 1)[1],
                             'b.sell_price(만원)':soup_wt_detail.find("div",class_="information").span.get_text().replace("만원",""),
                             'c.차량번호': s_thing[0].get_text(),
                             'd.연식(년월)': s_thing[1].get_text().replace('\xa0','').replace('년','').replace('월','').split("(")[0],
                             'e.주행거리(km)': s_thing[2].get_text().replace(",","").replace("km","").replace(" ",""),
                             'f.연료': s_thing[3].get_text().replace(",",""),
                             'g_1.배기량(cc)': s_thing[4].get_text().replace(" ","").replace(")","").split("(")[0].replace("cc",""),
                             'g_2.배기량(마력)': s_thing[4].get_text().replace(" ","").replace(")","").split("(")[1].replace("마력",""),
                             'h.변속기': s_thing[5].get_text().replace(",",""),
                             'i.색상': s_thing[6].get_text().replace(",","").replace(" ",""),
                             'j.사고유무': s_thing[7].get_text().replace('(사고이력조회)\n','').replace('\t',''),
                             'k.제조국':td_thing[0].get_text(),
                             'l.출시(년형)' : td_thing[1].get_text().split("/")[0].replace("년",""),
                             'm.신차가격(만원)' : td_thing[2].get_text().replace(',','').replace("만원",""),
                             'n.번호변경횟수' : d_thing[2].get_text().split(":")[1].replace(" ","").replace("회","").split("/")[0],
                             'o.소유자변경횟수' : d_thing[2].get_text().split(":")[1].replace(" ","").replace("회","").split("/")[1],
                             'p.보험사고이력(내차피해)_c' :  d_thing[4].get_text().replace(" ","").replace("보험사고이력(내차피해):","").split("회")[0],
                             'q.보험사고이력(내차피해)_m' :  d_thing[4].get_text().replace(" ","").replace("보험사고이력(내차피해):","").split("회")[1].replace(",","").replace("원",""),
                             'r.보험사고이력(타차가해)_c' :  d_thing[5].get_text().replace(" ","").replace("보험사고이력(타차가해):","").split("회")[0],
                             's.보험사고이력(타차가해)_m' :  d_thing[5].get_text().replace(" ","").replace("보험사고이력(타차가해):","").split("회")[1].replace(",","").replace("원",""),
                             't.연비(km/l)' : sp_thing[3].get_text().replace("km/ℓ",""),
                             'u.구동방식' : sp_thing[10].get_text().replace(" ",""),
                             'v.보디형식' : sp_thing[11].get_text(),
                             'w.변속기' : sp_thing[12].get_text()}     
                info.append(temp_dict)

            except:
                pass
        
 
    return DataFrame(info)


def concatthing(totpage):
    appended_data = []
    for k in range(totpage):
        try:
            progress(k+1,totpage,suffix='crawling car page')
            dfpg=my_car(k+1)
            appended_data.append(dfpg)
        
        except:
            pass
        
    appended_data = pd.concat(appended_data).reset_index(drop=True)
    
    return appended_data
        


used_car=concatthing(209)


used_car.to_csv('used_car_sago.csv',index=False)


ValueError: No objects to concatenate

In [47]:
from bs4 import BeautifulSoup
from urllib.request import urlopen
from pandas import Series, DataFrame
import pandas as pd
import sys

def progress(count, total, suffix=''):
    bar_len = 60
    filled_len = int(round(bar_len * count / float(total)))

    percents = round(100.0 * count / float(total), 1)
    bar = '#' * filled_len + '-' * (bar_len - filled_len)

    sys.stdout.write('|%s| %s%s ...%s\r' % (bar, percents, '%', suffix))
    sys.stdout.flush()  # As suggested by Rom Ruben


def get_soup(url):
    html_doc = urlopen(url).read()
    soup = BeautifulSoup(html_doc, 'html.parser')
    return soup


# x = {'a': if }
# x = {key: value for key, value in x.items() if value != 20}
# x



#승용차
def my_car(pagenum):
    site=f"https://www.bobaedream.co.kr/cyber/CyberCar.php?gubun=K&page={str(pagenum)}&order=S11&view_size=70"
    
    soup_wt=get_soup(site)
    info = []
#     num_carth=len(soup_wt.find("table",class_="cyber").tbody.find_all("a",class_="sub"))
    num_carth=len(soup_wt.find("body",class_="body-cyber-list").find_all("li",class_="product-item"))
    print(num_carth)
    
    for i in range(num_carth):
        soup_wt_detail = get_soup(str('http://www.bobaedream.co.kr')+soup_wt.find("body",class_="body-cyber-list").find_all("li",class_="product-item")[i])
        sp_thing=soup_wt_detail.find("div",class_="mode-cell fuel").find_all("td")
        s_thing = soup_wt_detail.find("div",class_="information").find_all("span",class_="s")
        td_thing=soup_wt_detail.find("table",class_="spectop").tbody.find_all("td")
        print(sp_thing)
        if soup_wt_detail.find("span",class_="fl").find_all("li")==[]:
            d_thing =0
            try:
                temp_dict = {}
                temp_dict = {'a_1.회사':soup_wt_detail.find("div",class_="tit").get_text().replace('\xa0\xa0\xa0','').split(None, 1)[0],
                             'a_2.모델명':soup_wt_detail.find("div",class_="tit").get_text().replace('\xa0\xa0\xa0','').split(None, 1)[1],
                             'b.sell_price(만원)':soup_wt_detail.find("div",class_="information").span.get_text().replace("만원",""),
                             'c.차량번호': s_thing[0].get_text(),
                             'd.연식(년월)': s_thing[1].get_text().replace('\xa0','').replace('년','').replace('월','').split("(")[0],
                             'e.주행거리(km)': s_thing[2].get_text().replace(",","").replace("km","").replace(" ",""),
                             'f.연료': s_thing[3].get_text().replace(",",""),
                             'g_1.배기량(cc)': s_thing[4].get_text().replace(" ","").replace(")","").split("(")[0].replace("cc",""),
                             'g_2.배기량(마력)': s_thing[4].get_text().replace(" ","").replace(")","").split("(")[1].replace("마력",""),
                             'h.변속기': s_thing[5].get_text().replace(",",""),
                             'i.색상': s_thing[6].get_text().replace(",","").replace(" ",""),
                             'j.사고유무': s_thing[7].get_text().replace('(사고이력조회)\n','').replace('\t',''),
                             'k.제조국':td_thing[0].get_text(),
                             'l.출시(년형)' : td_thing[1].get_text().split("/")[0].replace("년",""),
                             'm.신차가격(만원)' : td_thing[2].get_text().replace(',','').replace("만원",""),
                             'n.번호변경횟수' : "0",
                             'o.소유자변경횟수' : "0",
                             'p.보험사고이력(내차피해)_c' :  "0",
                             'q.보험사고이력(내차피해)_m' :  "0",
                             'r.보험사고이력(타차가해)_c' :  "0",
                             's.보험사고이력(타차가해)_m' :  "0",
                             't.연비(km/l)' : sp_thing[3].get_text().replace("km/ℓ",""),
                             'u.구동방식' : sp_thing[10].get_text().replace(" ",""),
                             'v.보디형식' : sp_thing[11].get_text(),
                             'w.변속기' : sp_thing[12].get_text()}     
                info.append(temp_dict)

            except:
                pass           
            
        else:
            
            d_thing = soup_wt_detail.find("span",class_="fl").find_all("li")

            try:
                temp_dict = {}
                temp_dict = {'a_1.회사':soup_wt_detail.find("div",class_="tit").get_text().replace('\xa0\xa0\xa0','').split(None, 1)[0],
                             'a_2.모델명':soup_wt_detail.find("div",class_="tit").get_text().replace('\xa0\xa0\xa0','').split(None, 1)[1],
                             'b.sell_price(만원)':soup_wt_detail.find("div",class_="information").span.get_text().replace("만원",""),
                             'c.차량번호': s_thing[0].get_text(),
                             'd.연식(년월)': s_thing[1].get_text().replace('\xa0','').replace('년','').replace('월','').split("(")[0],
                             'e.주행거리(km)': s_thing[2].get_text().replace(",","").replace("km","").replace(" ",""),
                             'f.연료': s_thing[3].get_text().replace(",",""),
                             'g_1.배기량(cc)': s_thing[4].get_text().replace(" ","").replace(")","").split("(")[0].replace("cc",""),
                             'g_2.배기량(마력)': s_thing[4].get_text().replace(" ","").replace(")","").split("(")[1].replace("마력",""),
                             'h.변속기': s_thing[5].get_text().replace(",",""),
                             'i.색상': s_thing[6].get_text().replace(",","").replace(" ",""),
                             'j.사고유무': s_thing[7].get_text().replace('(사고이력조회)\n','').replace('\t',''),
                             'k.제조국':td_thing[0].get_text(),
                             'l.출시(년형)' : td_thing[1].get_text().split("/")[0].replace("년",""),
                             'm.신차가격(만원)' : td_thing[2].get_text().replace(',','').replace("만원",""),
                             'n.번호변경횟수' : d_thing[2].get_text().split(":")[1].replace(" ","").replace("회","").split("/")[0],
                             'o.소유자변경횟수' : d_thing[2].get_text().split(":")[1].replace(" ","").replace("회","").split("/")[1],
                             'p.보험사고이력(내차피해)_c' :  d_thing[4].get_text().replace(" ","").replace("보험사고이력(내차피해):","").split("회")[0],
                             'q.보험사고이력(내차피해)_m' :  d_thing[4].get_text().replace(" ","").replace("보험사고이력(내차피해):","").split("회")[1].replace(",","").replace("원",""),
                             'r.보험사고이력(타차가해)_c' :  d_thing[5].get_text().replace(" ","").replace("보험사고이력(타차가해):","").split("회")[0],
                             's.보험사고이력(타차가해)_m' :  d_thing[5].get_text().replace(" ","").replace("보험사고이력(타차가해):","").split("회")[1].replace(",","").replace("원",""),
                             't.연비(km/l)' : sp_thing[3].get_text().replace("km/ℓ",""),
                             'u.구동방식' : sp_thing[10].get_text().replace(" ",""),
                             'v.보디형식' : sp_thing[11].get_text(),
                             'w.변속기' : sp_thing[12].get_text()}     
                info.append(temp_dict)

            except:
                pass
        
 
    return DataFrame(info)


def concatthing(totpage):
    appended_data = []
    for k in range(totpage):
        try:
            progress(k+1,totpage,suffix='crawling car page')
            dfpg=my_car(k+1)
            appended_data.append(dfpg)
        
        except:
            pass
        
    appended_data = pd.concat(appended_data).reset_index(drop=True)
    
    return appended_data
        


used_car=concatthing(1)


used_car.to_csv('used_car_sago.csv',index=False)


70 ----------------------------------------------------------------------------------------------------


ValueError: No objects to concatenate

In [46]:
site=f"https://www.bobaedream.co.kr/cyber/CyberCar.php?gubun=K&page={str(1)}&order=S11&view_size=70"
    
soup_wt=get_soup(site)
print(soup_wt.find("body",class_="body-cyber-list").find_all("li",class_="product-item"))

[<li class="product-item">
<div class="list-inner">
<div class="mode-cell thumb">
<a class="img w132" href="/cyber/CyberCar_view.php?no=765475&amp;gubun=K" target="_blank">
<img alt="현대 포터2 CRDi 슈퍼캡 초장축 스마트" src="//file2.bobaedream.co.kr/pds/CyberCar/5/765475/thum5_765475.jpg"/>
</a>
<div class="zzim btn-bookmark" onclick="qSet('zzim', '765475', 'C', 'K', this);">
<button class="btn-zzim" type="button">
<span class="icon-zzim">찜</span>
</button>
</div>
</div>
<div class="mode-cell title">
<p class="tit ellipsis">
<a href="/cyber/CyberCar_view.php?no=765475&amp;gubun=K" target="_blank" title="현대 포터2 CRDi 슈퍼캡 초장축 스마트">현대 포터2 CRDi 슈퍼캡 초장축 스마트</a>
</p>
<p class="stxt ellipsis"><a href="/cyber/CyberCar_view.php?no=765475&amp;gubun=K" target="_blank">무사고/오토미션/넉넉한 적재함, 실용만점 1톤트럭</a></p>
<dl class="data clearfix"><dt class="blind">모델 옵션</dt>

</dl>
</div>
<div class="mode-cell year">
<span class="text">17/05</span>
</div>
<div class="mode-cell fuel">
<span class="text">디젤</span>
</div>
<div cl

In [56]:
print(soup_wt.find("body",class_="body-cyber-list").find_all("li",class_="product-item")[0])

<li class="product-item">
<div class="list-inner">
<div class="mode-cell thumb">
<a class="img w132" href="/cyber/CyberCar_view.php?no=765475&amp;gubun=K" target="_blank">
<img alt="현대 포터2 CRDi 슈퍼캡 초장축 스마트" src="//file2.bobaedream.co.kr/pds/CyberCar/5/765475/thum5_765475.jpg"/>
</a>
<div class="zzim btn-bookmark" onclick="qSet('zzim', '765475', 'C', 'K', this);">
<button class="btn-zzim" type="button">
<span class="icon-zzim">찜</span>
</button>
</div>
</div>
<div class="mode-cell title">
<p class="tit ellipsis">
<a href="/cyber/CyberCar_view.php?no=765475&amp;gubun=K" target="_blank" title="현대 포터2 CRDi 슈퍼캡 초장축 스마트">현대 포터2 CRDi 슈퍼캡 초장축 스마트</a>
</p>
<p class="stxt ellipsis"><a href="/cyber/CyberCar_view.php?no=765475&amp;gubun=K" target="_blank">무사고/오토미션/넉넉한 적재함, 실용만점 1톤트럭</a></p>
<dl class="data clearfix"><dt class="blind">모델 옵션</dt>

</dl>
</div>
<div class="mode-cell year">
<span class="text">17/05</span>
</div>
<div class="mode-cell fuel">
<span class="text">디젤</span>
</div>
<div cla